In [43]:
# Support for math
import numpy as np
import math

# Plotting tools
from matplotlib import pyplot as plt
import matplotlib
from matplotlib import cm
import plotly.graph_objects as go
from plotly.subplots import make_subplots


import warnings
warnings.filterwarnings('ignore')

# File Tools for local
import pandas as pd
import sys

# Random seed for reproducibility
import random

import torch
# from botorch.models.gp_regression import HeteroskedasticSingleTaskGP - This was removed in path #2616.
from botorch.models.gp_regression import SingleTaskGP
from botorch.acquisition import qExpectedImprovement
from botorch.fit import fit_gpytorch_mll
from botorch.utils.transforms import normalize
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch.optim import optimize_acqf
from botorch.utils.transforms import normalize, unnormalize

from ipywidgets import interact, FloatSlider

#LHS sampling
#from pyDOE import lhs
from smt.sampling_methods import LHS
import random

# Cluster 
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler


>## Data Prep

In [44]:
df = pd.read_csv('parameterspace.csv')
df

n  theta    r     t  toughness    mass  printerid  campaignid   \
0      6      0  1.5  0.70   1.144667  1.7131          1            1   
1      6      0  1.5  1.05   1.607561  1.9386          2            1   
2      6      0  1.5  1.40   1.144338  1.9828          3            1   
3      6      0  1.7  0.70   3.642738  1.9723          4            1   
4      6      0  1.7  1.05   3.748405  2.2785          5            1   
...   ..    ...  ...   ...        ...     ...        ...          ...   
1795  12    200  2.3  1.05   1.358975  6.3430          5            3   
1796  12    200  2.3  1.40   3.196306  5.7742          1            3   
1797  12    200  2.5  0.70  36.104187  4.8745          2            3   
1798  12    200  2.5  1.05   1.313487  6.7221          4            3   
1799  12    200  2.5  1.40   1.069728  7.4933          5            3   

      category  
0            2  
1            2  
2            2  
3            2  
4            2  
...        ...  
1795         3  
1796         3  
1797         3  
1798         3  
1799         3  

[1800 rows x 9 columns]

In [45]:
x_inputs = df[['n',	'theta','r','t'] ].to_numpy()
y_outputs = df["toughness"].values.reshape(-1, 1)
# Set the device and dtype
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
dtype = torch.float32
# Convert to torch tensors
x_all = torch.tensor(x_inputs, dtype=torch.float32)
y_all = torch.tensor(y_outputs, dtype=torch.float32)


# Define a ground truth 
def ground_truth(x_query_batch: torch.Tensor):
    """
    x_query_batch: Tensor of shape (batch_size, d)
    Returns: Tensor of shape (batch_size, 1)
    """
    # x_all should be of shape (N, d)
    # Expand for broadcasting: (batch_size, N, d)
    diffs = x_all.unsqueeze(0) - x_query_batch.unsqueeze(1)  # (batch, N, d)
    dists = torch.norm(diffs, dim=2)  # (batch, N)
    idx = torch.argmin(dists, dim=1)  # (batch,)
    return y_all[idx]  # (batch, 1)



>## Initial Sampling Step

In [46]:
bounds = torch.tensor([[x_all[:, 0].min(), x_all[:, 0].max()],
                      [x_all[:, 1].min(), x_all[:, 1].max()],
                      [x_all[:, 2].min(), x_all[:, 2].max()],
                      [x_all[:, 3].min(), x_all[:, 3].max()]], dtype=torch.float32)

#bounds = torch.tensor([[0.0, 1.0], [0.0, 1.0], [0.0, 1.0], [0.0, 1.0]], dtype=torch.float32)

# Lets say theta is constrained 
# Bounds : sulf , anly, temp, time
xlimits = bounds.numpy()
sampling = LHS(xlimits=xlimits,random_state = np.random.RandomState(0))

num = 6
x = sampling(num)

lhs_data = pd.DataFrame(x, columns=['n','theta','r','t'])
# print(lhs_data.round(2))

# Select the 'temp' column for clustering
constrained = lhs_data[['theta']]

# Standardize the data (important for K-Means)
scaler = StandardScaler()
temp_data_scaled = scaler.fit_transform(constrained )

# Choose the number of clusters
num_clusters = 3

# Apply K-Means clustering
kmeans = KMeans(n_clusters=num_clusters, n_init=100, random_state=42)
lhs_data['cluster'] = kmeans.fit_predict(temp_data_scaled)

# Get cluster assignments and centroids
cluster_assignments = kmeans.labels_

# Get the centroids
centroids = scaler.inverse_transform(kmeans.cluster_centers_)

# Display the centroids
print("Centroids of Temperature Clusters:")
print(centroids)

# Replace the temperature values in lhs_data with the centroid temperatures for the designated clusters
for cluster in range(num_clusters):
    lhs_data.loc[lhs_data['cluster'] == cluster, 'theta'] = centroids[cluster][0]

# Display the updated lhs_data
print(lhs_data.round(2))


Centroids of Temperature Clusters:
[[166.66666667]
 [ 33.33333333]
 [100.        ]]
      n   theta     r     t  cluster
0  11.5  100.00  1.75  1.11        2
1   8.5   33.33  2.08  0.99        1
2   9.5  166.67  1.58  0.87        0
3  10.5  166.67  2.42  1.34        0
4   7.5  100.00  2.25  0.76        2
5   6.5   33.33  1.92  1.22        1


In [47]:
## Build Model A class 
class ModelA:
    def __init__(self, x_train, y_train, bounds):
        self.x_train = x_train
        self.y_train = y_train
        self.bounds = bounds
        self.model = self._fit_gp_model()
    
    def _fit_gp_model(self):
        model = SingleTaskGP(self.x_train, self.y_train)
        mll = ExactMarginalLogLikelihood(model.likelihood, model)
        fit_gpytorch_mll(mll)
        return model

    def gp_evaluate(self, test_x):
        self.model.eval()
        with torch.no_grad():
            posterior = self.model.posterior(test_x)
        mean = posterior.mean.squeeze().numpy()
        var = posterior.variance.squeeze().numpy()
        return mean, var

    def optimize_ei(self, batch_size=6):
        best_f = self.y_train.max()
        qEI = qExpectedImprovement(model=self.model, best_f=best_f)
        candidate, _ = optimize_acqf(
            acq_function=qEI,
            bounds=torch.tensor([[0., 0., 0. , 0.], [1., 1., 1.,1.]], dtype=self.x_train.dtype),
            q=batch_size,
            num_restarts=15,
            raw_samples=100,
        )
        return unnormalize(candidate, self.bounds)
    
    def new_candidates(self, feature='theta', num_clusters=3):
        candidates = self.optimize_ei().cpu().numpy()  # <-- fix is here
        data = {
            'n': candidates[:, 0],
            'theta': candidates[:, 1],
            'r': candidates[:, 2],
            't': candidates[:, 3]
        }
        data_df = pd.DataFrame(data)
        constrained = data_df[[feature]]
        scaler = StandardScaler()
        theta_data_scaled = scaler.fit_transform(constrained)

        kmeans = KMeans(n_clusters=num_clusters, n_init=100, random_state=42)
        data_df['cluster'] = kmeans.fit_predict(theta_data_scaled)
        centroids = scaler.inverse_transform(kmeans.cluster_centers_)

        for cluster in range(num_clusters):
            data_df.loc[data_df['cluster'] == cluster, feature] = centroids[cluster][0]

        return data_df.round(2)

class Plotting:
    def __init__(self, modelA: ModelA, variable_combinations):
        self.modelA = modelA
        self.x_train = modelA.x_train
        self.y_train = modelA.y_train
        self.bounds = modelA.bounds
        self.model = modelA.model
        self.variable_combinations = variable_combinations
        self.dtype = dtype

    def generate_input_data(self, A, B, c, d, combination):
        if combination == ('n', 'r', 't'):
            return torch.tensor(np.array([[A[i, j], d, B[i, j], c] for i in range(A.shape[0]) for j in range(A.shape[1])]), dtype=self.dtype)
        elif combination == ('theta', 'r', 't'):
            return torch.tensor(np.array([[d, A[i, j], B[i, j], c] for i in range(A.shape[0]) for j in range(A.shape[1])]), dtype=self.dtype)
        elif combination == ('n', 't', 'theta'):
            return torch.tensor(np.array([[A[i, j], c, B[i, j], d] for i in range(A.shape[0]) for j in range(A.shape[1])]), dtype=self.dtype)

    def create_slices(self, c_slices, d_fixed, combination):
        num_points = 20
        a = np.linspace(0, 1, num_points)
        b = np.linspace(0, 1, num_points)
        A, B = np.meshgrid(a, b)

        store_mean = []
        for d in d_fixed:
            mean_values = []
            for c in c_slices:
                input_data = self.generate_input_data(A, B, c, d, combination)
                mean, _ = self.modelA.gp_evaluate(input_data)
                mean_values.append(mean.reshape(A.shape))  # Reshape to grid
            store_mean.append(mean_values)

        return A, B, store_mean
    

    def sliced_plotting(self, combination, minmax, colormap='Viridis'):
        # Create slices for the fixed variable
        c_slices = np.linspace(0, 1, 12)
        d_fixed = [0, 0.25, 0.5, 0.75, 1.0]  # Fixed value for the other variable

        # Create a new figure with subplots for each combination
        fig = make_subplots(rows=1, cols=5, subplot_titles=('theta: 0', 'theta: 0.25','theta: 0.5', 'theta: 0.75','theta: 1.0'),
                        specs=[[{'type': 'surface'}, {'type': 'surface'},{'type': 'surface'}, {'type': 'surface'}, {'type': 'surface'}]])
        global_min = minmax[0].item()
        global_max = minmax[1].item()

        # Create slices and get mean values
        A, B, store_mean = self.create_slices(c_slices, d_fixed, combination)
        # Unpack the mean values for each slice
        mean_vals1, mean_vals2, mean_vals3, mean_vals4, mean_vals5 = store_mean[0], store_mean[1], store_mean[2], store_mean[3], store_mean[4]  

        for i, (c, y_grid1, y_grid2, y_grid3, y_grid4, y_grid5) in enumerate(zip(c_slices, mean_vals1,mean_vals2,mean_vals3,mean_vals4,mean_vals5), start=1):
            fig.add_trace(go.Surface(
                x=A,
                y=B,
                z=c * np.ones_like(A),  # Z-coordinate for slicing
                surfacecolor=y_grid1,  # Use predicted `y` as contour
                colorscale=colormap,
                cmin=global_min,
                cmax=global_max,
                showscale=True if i == 1 else False,  # Show color scale only on the first slice
                #   colorbar_x=0.45,
                opacity=0.7
            ), row=1, col=1)
    
            fig.add_trace(go.Surface(
                x=A,
                y=B,
                z=c * np.ones_like(A),  # Z-coordinate for slicing
                surfacecolor=y_grid2,  # Use predictediance as contour
                cmin=global_min,
                cmax=global_max,
                colorscale=colormap,
                showscale=True if i == 1 else False,  # Show color scale only on the first slice
                #colorbar_x=0.45,
                opacity=0.7
            ), row=1, col=2)

            fig.add_trace(go.Surface(
                x=A,
                y=B,
                z=c * np.ones_like(A),  # Z-coordinate for slicing
                surfacecolor=y_grid3,  # Use predictediance as contour
                cmin=global_min,
                cmax=global_max,
                colorscale=colormap,
                showscale=True if i == 1 else False,  # Show color scale only on the first slice
                opacity=0.7
            ), row=1, col=3)

            fig.add_trace(go.Surface(
                x=A,
                y=B,
                z=c * np.ones_like(A),  # Z-coordinate for slicing
                surfacecolor=y_grid4,  # Use predictediance as contour
                cmin=global_min,
                cmax=global_max,
                colorscale=colormap,
                showscale=True if i == 1 else False,  # Show color scale only on the first slice
                opacity=0.7
            ), row=1, col=4)

            fig.add_trace(go.Surface(
                x=A,
                y=B,
                z=c * np.ones_like(A),  # Z-coordinate for slicing
                surfacecolor=y_grid5,  # Use predictediance as contour
                cmin=global_min,
                cmax=global_max,
                colorscale=colormap,
                showscale=True if i == 1 else False,  # Show color scale only on the first slice
                opacity=0.7
            ), row=1, col=5)
            
        fig.update_layout(
            height=400,
            width=1300,
            margin=dict(l=50, r=50, b=50, t=50),
            scene=dict(
                xaxis_title=combination[0],
                yaxis_title=combination[1],
                zaxis_title=combination[2]
            ),
            scene2=dict(
                xaxis_title=combination[0],
                yaxis_title=combination[1],
                zaxis_title=combination[2]
            ),
            scene3=dict(
                xaxis_title=combination[0],
                yaxis_title=combination[1],
                zaxis_title=combination[2]
            ),
            scene4=dict(
                xaxis_title=combination[0],
                yaxis_title=combination[1],
                zaxis_title=combination[2]
            ),
            scene5=dict(
                xaxis_title=combination[0],
                yaxis_title=combination[1],
                zaxis_title=combination[2]
            )
        )

        fig.show()





In [48]:
original_bounds = torch.tensor([[x_all[:,0].min(), x_all[:,1].min(), x_all[:,2].min(), x_all[:,3].min()], [x_all[:,0].max(), x_all[:,1].max(), x_all[:,2].max(), x_all[:,3].max()]])
x_train = torch.tensor(lhs_data[['n','theta','r','t']].values, dtype=torch.float32)
nx_train = normalize(x_train, bounds=original_bounds)
y_train = ground_truth(x_train)

# Step 1: Initialize your model
modelA = ModelA(x_train=nx_train, y_train=y_train, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_train.min(),y_train.max()]
plotting.sliced_plotting(combination, minmax)

# Step 1: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
       n       theta     r     t  cluster
0  12.00  115.339996  1.81  0.72        0
1   6.00  146.639999  2.45  0.70        1
2   6.00   81.300003  2.50  0.70        2
3   7.34  115.339996  1.70  0.70        0
4  11.14  115.339996  2.30  0.75        0
5   6.00  115.339996  1.95  0.87        0


In [49]:
x_train1 = torch.tensor(new_candidates[['n','theta','r','t']].values, dtype=torch.float32)
nx_train1 = normalize(x_train1, bounds=original_bounds)
y_train1 = ground_truth(x_train1)

# Combine the new data with the existing data
x_combined = torch.cat((nx_train, nx_train1), dim=0)
y_combined = torch.cat((y_train, y_train1), dim=0)

# Step 1: Instantiate and train model
modelA = ModelA(x_train=x_combined, y_train=y_combined, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_combined.min(),y_combined.max()]
plotting.sliced_plotting(combination, minmax)

# Step 3: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
       n       theta     r     t  cluster
0  10.32  100.480003  2.29  0.89        0
1   9.41  127.089996  2.32  0.70        2
2  11.97  100.480003  2.09  0.70        0
3  12.00  127.089996  2.07  0.74        2
4  10.15  100.480003  2.16  0.70        0
5  12.00  149.479996  1.78  0.77        1


In [50]:
x_train2 = torch.tensor(new_candidates[['n','theta','r','t']].values, dtype=torch.float32)
nx_train2 = normalize(x_train2, bounds=original_bounds)
y_train2 = ground_truth(x_train2)

# Combine the new data with the existing data
x_combined = torch.cat((nx_train, nx_train1,nx_train2), dim=0)
y_combined = torch.cat((y_train, y_train1,y_train2), dim=0)


# Step 1: Instantiate and train model
modelA = ModelA(x_train=x_combined, y_train=y_combined, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_combined.min(),y_combined.max()]
plotting.sliced_plotting(combination, minmax)

# Step 3: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
       n       theta     r     t  cluster
0  12.00   66.169998  2.18  0.70        1
1  12.00   66.169998  2.24  0.70        1
2  12.00  200.000000  1.54  1.36        0
3  12.00   66.169998  2.04  0.70        1
4  10.61  152.509995  2.49  1.26        2
5  12.00  200.000000  1.50  0.70        0


In [51]:
x_train3 = torch.tensor(new_candidates[['n','theta','r','t']].values, dtype=torch.float32)
nx_train3 = normalize(x_train2, bounds=original_bounds)
y_train3 = ground_truth(x_train2)

# Combine the new data with the existing data
x_combined = torch.cat((nx_train, nx_train1,nx_train2, nx_train3), dim=0)
y_combined = torch.cat((y_train, y_train1,y_train2,y_train3), dim=0)


# Step 1: Instantiate and train model
modelA = ModelA(x_train=x_combined, y_train=y_combined, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_combined.min(),y_combined.max()]
plotting.sliced_plotting(combination, minmax)

# Step 3: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
       n       theta     r     t  cluster
0  12.00    0.000000  1.50  1.40        2
1   7.80  180.229996  2.33  0.70        1
2  12.00   59.410000  2.07  0.70        0
3   8.18  180.229996  2.50  0.91        1
4  12.00  180.229996  1.50  0.70        1
5  12.00   59.410000  2.26  0.70        0


In [52]:
x_train4 = torch.tensor(new_candidates[['n','theta','r','t']].values, dtype=torch.float32)
nx_train4 = normalize(x_train2, bounds=original_bounds)
y_train4 = ground_truth(x_train2)

# Combine the new data with the existing data
x_combined = torch.cat((nx_train, nx_train1,nx_train2, nx_train3,nx_train4), dim=0)
y_combined = torch.cat((y_train, y_train1,y_train2,y_train3,y_train4), dim=0)


# Step 1: Instantiate and train model
modelA = ModelA(x_train=x_combined, y_train=y_combined, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_combined.min(),y_combined.max()]
plotting.sliced_plotting(combination, minmax)

# Step 3: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
       n       theta     r     t  cluster
0  12.00   74.739998  2.08  0.70        2
1  12.00   95.559998  2.20  0.70        0
2  11.82  198.509995  1.50  0.70        1
3  12.00   74.739998  2.18  0.91        2
4  12.00   74.739998  2.29  0.70        2
5   9.21   95.559998  2.50  0.70        0


In [53]:
x_train5 = torch.tensor(new_candidates[['n','theta','r','t']].values, dtype=torch.float32)
nx_train5 = normalize(x_train2, bounds=original_bounds)
y_train5 = ground_truth(x_train2)

# Combine the new data with the existing data
x_combined = torch.cat((nx_train, nx_train1,nx_train2, nx_train3,nx_train4,nx_train5), dim=0)
y_combined = torch.cat((y_train, y_train1,y_train2,y_train3,y_train4,y_train5), dim=0)


# Step 1: Instantiate and train model
modelA = ModelA(x_train=x_combined, y_train=y_combined, bounds=original_bounds)

# Step 2: Initialize Plotting class
variable_combinations = [('n', 'r', 't'), ('theta', 'r', 't'), ('n', 't', 'theta')]
plotting = Plotting(modelA=modelA, variable_combinations=variable_combinations)

combination = variable_combinations[0]

minmax = [y_combined.min(),y_combined.max()]
plotting.sliced_plotting(combination, minmax)

# Step 3: Get the next candidates
new_candidates = modelA.new_candidates(feature='theta', num_clusters=3)
print("New Candidates:")
print(new_candidates.round(2))


New Candidates:
      n       theta     r     t  cluster
0  12.0   87.389999  2.34  0.70        0
1  12.0   87.389999  2.20  0.70        0
2  12.0   71.900002  2.04  0.70        1
3   9.0  105.269997  2.50  0.70        2
4  12.0   71.900002  2.21  0.70        1
5  12.0   87.389999  2.19  0.91        0
